# PART 2: EXPLORATORY DATA ANALYSIS

**Objective:** This notebook will explore the generated datasets to draw insights from the patient visits and any relationships between date/times to inform our scheduling & streaming models.

---

In [1]:
# Data Management & Manipulation
import numpy as np
import pandas as pd

# Data Visualization
import geopandas as gpd
import folium
import folium.plugins as plugins
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns
from plotly.subplots import make_subplots

# Utils
from datetime import datetime, timedelta
import ipywidgets as widgets
import random
import warnings
from IPython.display import display, HTML
from ipywidgets import interact, interact_manual
from time import sleep
%matplotlib inline
sns.set_style('white')
sns.set_color_codes()
plt.style.use('default')  # sub 'dark_background'
warnings.filterwarnings("ignore")

---
---

## 2A: Setup

**Objective**: Read in patients and clinic data for exploratory analysis.

---

In [2]:
patients_df = pd.read_csv('./uc_past_patients.csv', index_col='pt_id')
patients_df

pt_name      pt_dob  pt_age visit_location  \
pt_id                                                               
1000004  Christopher Clark Jr.  2021-11-01       0         denver   
1000014             Janet Rowe  1969-05-13      52         denver   
1000016        Anthony Johnson  1990-07-06      31         denver   
1000007           Debra Huerta  1963-10-30      58         denver   
1000010           Paul Hammond  1974-07-10      47         denver   
...                        ...         ...     ...            ...   
5023227               Kyle Lam  1956-11-04      65       lakewood   
5023219             Jason Tate  1990-08-10      31       lakewood   
5023224         Peggy Williams  2016-12-03       5       lakewood   
5023230           Anthony Reid  1992-08-11      29       lakewood   
5023223          Drew Randolph  2016-11-12       5       lakewood   

           visit_reason  visit_code  visit_date visit_day checkin_time  \
pt_id                                                                    
1000004    rash/allergy           5  2021-05-01  Saturday     10:46:44   
1000014     vaccination           3  2021-05-01  Saturday     10:53:58   
1000016           cough           4  2021-05-01  Saturday     11:02:39   
1000007  cold/flu/fever           4  2021-05-01  Saturday     11:09:27   
1000010       drug-test           3  2021-05-01  Saturday     11:29:30   
...                 ...         ...         ...       ...          ...   
5023227    stomach-pain           5  2022-04-30  Saturday     19:33:08   
5023219        diarrhea           5  2022-04-30  Saturday     19:34:20   
5023224      covid-test           4  2022-04-30  Saturday     19:40:07   
5023230       drug-test           3  2022-04-30  Saturday     19:40:45   
5023223    rash/allergy           5  2022-04-30  Saturday     19:48:28   

        checkout_time  rolling_ct  rolling_code  
pt_id                                            
1000004      11:34:44           1           0.0  
1000014      12:04:58           2           5.0  
1000016      12:08:39           3           4.0  
1000007      12:29:27           4           4.0  
1000010      12:30:30           3           4.5  
...               ...         ...           ...  
5023227      21:24:08           9           4.8  
5023219      21:17:20          10           4.8  
5023224      20:44:07          11           4.8  
5023230      20:46:45          12           4.7  
5023223      21:14:28          13           4.6  

[109416 rows x 12 columns]

In [3]:
clinics_df = pd.read_csv('./uc_clinics.csv', index_col='branch_name')
clinics_df

lat         lon  to_denver  to_edgewater  to_wheatridge  \
branch_name                                                                  
denver       39.739064 -104.989697        0.0           5.1            6.3   
edgewater    39.753954 -105.067788        5.0           0.0            2.0   
wheatridge   39.766857 -105.081983        6.3           2.0            0.0   
rino         39.767328 -104.981132        1.9           7.8            7.5   
lakewood     39.704552 -105.079883        7.5           4.3           12.0   

             to_rino  to_lakewood  \
branch_name                         
denver           2.0          8.0   
edgewater        7.7          4.4   
wheatridge       7.8          4.8   
rino             0.0         10.7   
lakewood        11.0          0.0   

                                                nearby_clinics  
branch_name                                                     
denver                     [('rino', 2.0), ('edgewater', 5.1)]  
edgewater    [('wheatridge', 2.0), ('lakewood', 4.4), ('den...  
wheatridge             [('edgewater', 2.0), ('lakewood', 4.8)]  
rino                                         [('denver', 1.9)]  
lakewood                                  [('edgewater', 4.3)]

---
---

## 2B: Initial Explorations

**Objective**: Conduct initial explorations on the raw data without further aggregation or feature engineering.

---

#### Examine data characteristics & summary statistics of patient records:

In [4]:
patients_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 109416 entries, 1000004 to 5023223
Data columns (total 12 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   pt_name         109416 non-null  object 
 1   pt_dob          109416 non-null  object 
 2   pt_age          109416 non-null  int64  
 3   visit_location  109416 non-null  object 
 4   visit_reason    109416 non-null  object 
 5   visit_code      109416 non-null  int64  
 6   visit_date      109416 non-null  object 
 7   visit_day       109416 non-null  object 
 8   checkin_time    109416 non-null  object 
 9   checkout_time   109416 non-null  object 
 10  rolling_ct      109416 non-null  int64  
 11  rolling_code    109416 non-null  float64
dtypes: float64(1), int64(3), object(8)
memory usage: 10.9+ MB


In [5]:
# Get descriptive stats of continuous variables
patients_df[['pt_age', 'rolling_ct']].describe()

pt_age     rolling_ct
count  109416.000000  109416.000000
mean       34.481831       5.339831
std        20.864053       2.840170
min         0.000000       1.000000
25%        18.000000       3.000000
50%        32.000000       5.000000
75%        50.000000       7.000000
max        80.000000      22.000000

#### Visually explore value counts & distributions:

In [6]:
fig = make_subplots(
    rows=1, cols=2, 
    specs=[[{'type':'domain'}, {'type':'xy'}]], 
    column_widths=[0.35, 0.65], 
    subplot_titles=['Patient Distribution by Clinic', 'Location Breakdown by Severity']
)

# Construct pie-chart based on patient count for each clinic location
location_counts = patients_df['visit_location'].value_counts()
pie = go.Pie(values=location_counts, labels=location_counts.index.str.capitalize(), textinfo='label+percent', showlegend=False)

# Construct histogram for patient count by location stratified by severity level
hist1 = go.Histogram(x=patients_df[patients_df.visit_code==3]['visit_location'], name='Level 3', marker_color='khaki')
hist2 = go.Histogram(x=patients_df[patients_df.visit_code==4]['visit_location'], name='Level 4', marker_color='coral')
hist3 = go.Histogram(x=patients_df[patients_df.visit_code==5]['visit_location'], name='Level 5', marker_color='firebrick')

# Add subplots to figure object
fig.add_trace(pie, row=1, col=1)
fig.add_trace(hist3, row=1, col=2)
fig.add_trace(hist2, row=1, col=2)
fig.add_trace(hist1, row=1, col=2)

# Output figure with custom modifications
fig.update_layout(height=600, width=1100, showlegend=True, barmode='stack')
fig.show()

The figure above...

In [7]:
df = patients_df.copy().sort_values(by='visit_code')
fig = px.histogram(df, x='visit_reason', text_auto=True, color='visit_code', color_discrete_sequence=['khaki', 'coral', 'firebrick'])
fig.update_layout(height=600, width=1200, title_text='Patient Count by Reason')
fig.update_xaxes(categoryorder='total ascending')
fig.show()

The figure above...

In [8]:
fig = px.histogram(patients_df, x='pt_age', text_auto=False, color_discrete_sequence=['darkcyan'])
fig.update_layout(height=400, width=1000, title_text='Patient Count by Age')
fig.show()

The figure above...

---
---

## 2C: Aggregated Explorations

**Objective**: Closely examine relationships within the dataset through aggregated groupings & feature engineering.

---

In [9]:
patients_df

pt_name      pt_dob  pt_age visit_location  \
pt_id                                                               
1000004  Christopher Clark Jr.  2021-11-01       0         denver   
1000014             Janet Rowe  1969-05-13      52         denver   
1000016        Anthony Johnson  1990-07-06      31         denver   
1000007           Debra Huerta  1963-10-30      58         denver   
1000010           Paul Hammond  1974-07-10      47         denver   
...                        ...         ...     ...            ...   
5023227               Kyle Lam  1956-11-04      65       lakewood   
5023219             Jason Tate  1990-08-10      31       lakewood   
5023224         Peggy Williams  2016-12-03       5       lakewood   
5023230           Anthony Reid  1992-08-11      29       lakewood   
5023223          Drew Randolph  2016-11-12       5       lakewood   

           visit_reason  visit_code  visit_date visit_day checkin_time  \
pt_id                                                                    
1000004    rash/allergy           5  2021-05-01  Saturday     10:46:44   
1000014     vaccination           3  2021-05-01  Saturday     10:53:58   
1000016           cough           4  2021-05-01  Saturday     11:02:39   
1000007  cold/flu/fever           4  2021-05-01  Saturday     11:09:27   
1000010       drug-test           3  2021-05-01  Saturday     11:29:30   
...                 ...         ...         ...       ...          ...   
5023227    stomach-pain           5  2022-04-30  Saturday     19:33:08   
5023219        diarrhea           5  2022-04-30  Saturday     19:34:20   
5023224      covid-test           4  2022-04-30  Saturday     19:40:07   
5023230       drug-test           3  2022-04-30  Saturday     19:40:45   
5023223    rash/allergy           5  2022-04-30  Saturday     19:48:28   

        checkout_time  rolling_ct  rolling_code  
pt_id                                            
1000004      11:34:44           1           0.0  
1000014      12:04:58           2           5.0  
1000016      12:08:39           3           4.0  
1000007      12:29:27           4           4.0  
1000010      12:30:30           3           4.5  
...               ...         ...           ...  
5023227      21:24:08           9           4.8  
5023219      21:17:20          10           4.8  
5023224      20:44:07          11           4.8  
5023230      20:46:45          12           4.7  
5023223      21:14:28          13           4.6  

[109416 rows x 12 columns]

#### Explore daily patient count aggregated by the day of the week:

In [10]:
# Track the number of days in past year broken down by the day of the week
uniq_days = patients_df.groupby(['visit_date', 'visit_day']).count().reset_index(drop=False)[['visit_date', 'visit_day']]
uniq_days.visit_day.value_counts()

Saturday     53
Sunday       52
Monday       52
Tuesday      52
Wednesday    52
Thursday     52
Friday       52
Name: visit_day, dtype: int64

In [11]:
# Aggregate patients data based on daily count broken down by location and day of week
num_pts_per_day = patients_df.groupby(['visit_location', 'visit_day']).count()[['rolling_ct']].reset_index(drop=False)
num_pts_per_day['avg_num_pts'] = num_pts_per_day[['rolling_ct', 'visit_day']].apply(lambda x: round(x[0]/53, 1) if x[1] in ['Saturday'] else round(x[0]/52, 1), axis=1)

# Sort value types for plot outputs to be in desired order
num_pts_per_day['order'] = num_pts_per_day.visit_day.map({'Monday': 0, 'Tuesday': 1, 'Wednesday': 2, 'Thursday': 3, 'Friday': 4, 'Saturday': 5, 'Sunday': 6})
num_pts_per_day = num_pts_per_day.sort_values(by='order')

# Plot average number of patients broken down by day of week, stratified by location
fig = px.bar(
    num_pts_per_day, x='visit_day', y='avg_num_pts', 
    color='visit_location', barmode='group', 
    text='avg_num_pts', title='Average Number of Patients per Day & Clinic',
    labels={'visit_day': 'Day of the Week', 'avg_num_pts': 'Avg. Number of Patients'}
)
fig.update_traces(textposition='outside', cliponaxis=False, textfont_size=10)
fig.show()

The figure above shows...

#### Explore differences between weekday vs. weekend:

In [12]:
# Create attribute of boolean representing if visit_day falls on Saturday/Sunday
patients_df['weekend'] = patients_df.visit_day.map(lambda x: 1 if x in ['Saturday', 'Sunday'] else 0)

# Aggregate patients day based on visit_day falling on weekday or weekend
weekend_df = patients_df.groupby(['visit_location', 'weekend']).count()[['rolling_ct']].reset_index(drop=False)
weekend_df['avg_num_pts'] = weekend_df[['rolling_ct', 'weekend']] \
    .apply(lambda x: round(x[0]/105, 1) if x[1] == 1 else round(x[0]/260, 1), axis=1)

# Plot average number of patients on weekdays and weekends, broken down by location
fig = px.bar(
    weekend_df, x='weekend', y='avg_num_pts', 
    color='visit_location', barmode='group', 
    text='avg_num_pts', title='Average Number of Patients Per Clinic (Weekdays vs Weekend)',
    labels={'weekend': 'Day Type', 'avg_num_pts': 'Avg. Number of Patients'}
)
for idx in range(len(fig.data)):
    fig.data[idx].x = ['Weekday', 'Weekend']
fig.update_traces(textposition='outside', cliponaxis=False, textfont_size=10)
fig.show()

The figure above shows...

In [13]:
patients_df

pt_name      pt_dob  pt_age visit_location  \
pt_id                                                               
1000004  Christopher Clark Jr.  2021-11-01       0         denver   
1000014             Janet Rowe  1969-05-13      52         denver   
1000016        Anthony Johnson  1990-07-06      31         denver   
1000007           Debra Huerta  1963-10-30      58         denver   
1000010           Paul Hammond  1974-07-10      47         denver   
...                        ...         ...     ...            ...   
5023227               Kyle Lam  1956-11-04      65       lakewood   
5023219             Jason Tate  1990-08-10      31       lakewood   
5023224         Peggy Williams  2016-12-03       5       lakewood   
5023230           Anthony Reid  1992-08-11      29       lakewood   
5023223          Drew Randolph  2016-11-12       5       lakewood   

           visit_reason  visit_code  visit_date visit_day checkin_time  \
pt_id                                                                    
1000004    rash/allergy           5  2021-05-01  Saturday     10:46:44   
1000014     vaccination           3  2021-05-01  Saturday     10:53:58   
1000016           cough           4  2021-05-01  Saturday     11:02:39   
1000007  cold/flu/fever           4  2021-05-01  Saturday     11:09:27   
1000010       drug-test           3  2021-05-01  Saturday     11:29:30   
...                 ...         ...         ...       ...          ...   
5023227    stomach-pain           5  2022-04-30  Saturday     19:33:08   
5023219        diarrhea           5  2022-04-30  Saturday     19:34:20   
5023224      covid-test           4  2022-04-30  Saturday     19:40:07   
5023230       drug-test           3  2022-04-30  Saturday     19:40:45   
5023223    rash/allergy           5  2022-04-30  Saturday     19:48:28   

        checkout_time  rolling_ct  rolling_code  weekend  
pt_id                                                     
1000004      11:34:44           1           0.0        1  
1000014      12:04:58           2           5.0        1  
1000016      12:08:39           3           4.0        1  
1000007      12:29:27           4           4.0        1  
1000010      12:30:30           3           4.5        1  
...               ...         ...           ...      ...  
5023227      21:24:08           9           4.8        1  
5023219      21:17:20          10           4.8        1  
5023224      20:44:07          11           4.8        1  
5023230      20:46:45          12           4.7        1  
5023223      21:14:28          13           4.6        1  

[109416 rows x 13 columns]

In [14]:
# Create appt_time column (in minutes)
patients_df['appt_time'] = patients_df[['checkin_time', 'checkout_time']] \
    .apply(lambda x: datetime.strptime(x[1], '%H:%M:%S') - datetime.strptime(x[0], '%H:%M:%S'), axis=1) \
    .apply(lambda x: int(x.seconds/60))
patients_df

pt_name      pt_dob  pt_age visit_location  \
pt_id                                                               
1000004  Christopher Clark Jr.  2021-11-01       0         denver   
1000014             Janet Rowe  1969-05-13      52         denver   
1000016        Anthony Johnson  1990-07-06      31         denver   
1000007           Debra Huerta  1963-10-30      58         denver   
1000010           Paul Hammond  1974-07-10      47         denver   
...                        ...         ...     ...            ...   
5023227               Kyle Lam  1956-11-04      65       lakewood   
5023219             Jason Tate  1990-08-10      31       lakewood   
5023224         Peggy Williams  2016-12-03       5       lakewood   
5023230           Anthony Reid  1992-08-11      29       lakewood   
5023223          Drew Randolph  2016-11-12       5       lakewood   

           visit_reason  visit_code  visit_date visit_day checkin_time  \
pt_id                                                                    
1000004    rash/allergy           5  2021-05-01  Saturday     10:46:44   
1000014     vaccination           3  2021-05-01  Saturday     10:53:58   
1000016           cough           4  2021-05-01  Saturday     11:02:39   
1000007  cold/flu/fever           4  2021-05-01  Saturday     11:09:27   
1000010       drug-test           3  2021-05-01  Saturday     11:29:30   
...                 ...         ...         ...       ...          ...   
5023227    stomach-pain           5  2022-04-30  Saturday     19:33:08   
5023219        diarrhea           5  2022-04-30  Saturday     19:34:20   
5023224      covid-test           4  2022-04-30  Saturday     19:40:07   
5023230       drug-test           3  2022-04-30  Saturday     19:40:45   
5023223    rash/allergy           5  2022-04-30  Saturday     19:48:28   

        checkout_time  rolling_ct  rolling_code  weekend  appt_time  
pt_id                                                                
1000004      11:34:44           1           0.0        1         48  
1000014      12:04:58           2           5.0        1         71  
1000016      12:08:39           3           4.0        1         66  
1000007      12:29:27           4           4.0        1         80  
1000010      12:30:30           3           4.5        1         61  
...               ...         ...           ...      ...        ...  
5023227      21:24:08           9           4.8        1        111  
5023219      21:17:20          10           4.8        1        103  
5023224      20:44:07          11           4.8        1         64  
5023230      20:46:45          12           4.7        1         66  
5023223      21:14:28          13           4.6        1         86  

[109416 rows x 14 columns]

In [15]:
# Average appointment time per reason, per location
patients_df.groupby(['visit_location', 'visit_reason']).mean()['appt_time']

visit_location  visit_reason      
denver          UTI                    85.181613
                ache/pain              70.417722
                blood/lab-work         70.663221
                chest-pain            100.223026
                cold/flu/fever         85.380356
                                         ...    
wheatridge      rash/allergy           84.885370
                sore-throat            69.752740
                stomach-pain           98.670854
                vaccination            59.522880
                weakness/dizziness     99.817039
Name: appt_time, Length: 100, dtype: float64

In [16]:
# Average appointment time per visit code, per location
patients_df.groupby(['visit_location', 'visit_code']).mean()['appt_time']

visit_location  visit_code
denver          3             63.040506
                4             73.834057
                5             95.792340
edgewater       3             61.452309
                4             71.994223
                5             93.761985
lakewood        3             62.828819
                4             73.629744
                5             95.435102
rino            3             61.900784
                4             72.545650
                5             94.499532
wheatridge      3             62.318182
                4             73.266563
                5             94.883351
Name: appt_time, dtype: float64

In [17]:
# Overall average appointment time
patients_df.groupby('visit_reason').mean()['appt_time']

visit_reason
UTI                    84.436460
ache/pain              69.532690
blood/lab-work         69.747126
chest-pain             99.509873
cold/flu/fever         84.513336
cough                  69.530643
covid-test             59.506875
cuts/abscess           84.812500
diarrhea              100.046703
drug-test              59.554390
ear-pain               69.619429
headache               84.654192
injury/accident        99.494141
physical               60.183883
pink-eye               69.630366
rash/allergy           84.678665
sore-throat            69.522537
stomach-pain           99.616323
vaccination            59.683296
weakness/dizziness     99.859583
Name: appt_time, dtype: float64

In [18]:
# Average appointment time per day of week in each clinic
patients_df.groupby(['visit_location','visit_day']).mean()['appt_time']

visit_location  visit_day
denver          Friday       77.217795
                Monday       78.102083
                Saturday     78.142179
                Sunday       78.265852
                Thursday     77.862845
                Tuesday      78.234082
                Wednesday    77.146934
edgewater       Friday       75.897070
                Monday       75.921456
                Saturday     76.120403
                Sunday       76.248530
                Thursday     76.166992
                Tuesday      75.715394
                Wednesday    75.967925
lakewood        Friday       77.501367
                Monday       78.189067
                Saturday     77.691589
                Sunday       76.912595
                Thursday     77.527516
                Tuesday      77.684401
                Wednesday    77.756105
rino            Friday       76.289419
                Monday       76.160308
                Saturday     76.429834
                Sunday       77.359364

---
---

## 2_: Daily Influx Explorations

**Objective**: Visually explore patient influx rate to inform scheduler process.

---

In [19]:
# Create iterable objects that are desired for toggle menus
locations = patients_df.visit_location.unique().tolist()
dates = patients_df.visit_date.unique().tolist()

@interact
def generate_daily_dist(date=dates, first_location=locations, second_location=locations):
    """Produces rolling-count distributions that can be toggled through for specific locations & dates."""
    
    # Convert specific times to grouped versions
    df = patients_df.copy()
    df['checkin_time'] = df.checkin_time.apply(lambda x: x[:-3])
    
    # Create subset data for desired date and the two locations to compare
    df1 = df[(df.visit_date == date) & (df.visit_location == first_location)]
    df2 = df[(df.visit_date == date) & (df.visit_location == second_location)]

    # Construct plot for each subset 
    fig = go.Figure()
    
    # Construct barplot for patient count by location stratified by severity level
    fig = go.Figure()
    bar1 = go.Bar(
        x=df1['checkin_time'], y=df1['rolling_ct'], 
        name=f'Pt. Count @ {first_location.capitalize()} clinic', marker_color='red'
    )
    bar2 = go.Bar(
        x=df2['checkin_time'], y=df2['rolling_ct'], 
        name=f'Pt. Count @ {second_location.capitalize()} clinic', marker_color='blue'
    )

    # Add subplots to figure object
    fig.add_trace(bar1)
    fig.add_trace(bar2)

    # Output figure with custom modifications
    order = sorted(df1.checkin_time.tolist() + df2.checkin_time.tolist())
    fig.update_xaxes(categoryorder='array', categoryarray=order)
    fig.update_traces(opacity=0.3)
    fig.update_layout(height=500, width=1200, showlegend=True, barmode='overlay')
    fig.show()

interactive(children=(Dropdown(description='date', options=('2021-05-01', '2021-05-02', '2021-05-03', '2021-05…

The interactive widget above lets us explore the rolling patient count of two clinics for any date to examine the influx patterns....

---
---

## 2_: Geographic Explorations

**Objective**: Explore dataset attributes within a geospatial context.

---

#### Construct Folium map that indicates a clinic's patient influx for a particular date & time:

In [20]:
# Create iterable objects that are desired for toggle menus
dates = patients_df.visit_date.unique().tolist()
times = { '08': '8am', '09': '9am', '10': '10am', '11': '11am', '12': '12pm', '13': '1pm', 
          '14': '2pm', '15': '3pm', '16': '4pm', '17': '5pm', '18': '6pm', '19': '7pm', '20': '8pm'}

@interact
def map_daily_influx(date=dates, time=list(times.values())):
    """Produces Folium map of each clinic with indicated influx level based on date & time of interest."""
    
    df = patients_df.copy()
    
    # Bin check-in times by hour and get max rolling_ct of hour for simpler visual
    df['checkin_time'] = df.checkin_time.apply(lambda x: x[:2])
    df['checkin_time'] = df.checkin_time.map(times)
    df = df.groupby(['visit_location', 'visit_date', 'checkin_time']).max()[['rolling_ct']].reset_index(drop=False)
    
    # Gather clinic coordinates for map
    df['lat'] = df.visit_location.map(clinics_df.to_dict()['lat'])
    df['lon'] = df.visit_location.map(clinics_df.to_dict()['lon'])
    
    # Filter dataframe based on desired input date and time
    df = df[(df.visit_date == date) & (df.checkin_time == time)]
    
    # Duplicate records based on rolling count of patients for cluster-map
    df = df.loc[df.index.repeat(df['rolling_ct'])]

    # Instantiate Folium map based on Denver, CO's base coordinates
    m = folium.Map(location=[39.74, -105], zoom_start=13, min_zoom=10, max_zoom=14)
    marker = plugins.MarkerCluster(name='Patient Count').add_to(m)
    
    # Add a marker for every record in the filtered data, use a clustered view
    for row in df.iterrows():
        folium.Marker(location=[row[1]['lat'], row[1]['lon']]).add_to(marker)
    
    folium.LayerControl().add_to(m)

    display(m)

interactive(children=(Dropdown(description='date', options=('2021-05-01', '2021-05-02', '2021-05-03', '2021-05…

The interactive widget above lets us visualize the geographic locations of each clinic & explore the rolling patient count at any desired time....

---
---

## 2_: 

**Objective**: 

---